# Uczenie reprezentacji projekt - MIDI
Autorzy:
- Dawid Zieliński 266880
- Bartosz Sierzputowski 266599

## Opis problemu

### Dane wejściowe
Wykorzystujemy zbiór [GiantMIDI-Piano](https://github.com/bytedance/GiantMIDI-Piano) składający się z 10 855 piosenek w formacie midi (.mid). \
Ze względu na występowania w nim bardzo wielu kompozytorów, w tym wielu takich o jednym utworze, postanowiliśmy ograniczyć problem do klasyfikacji 20 kompozytorów o największej liczbie utworów i pracować na zbiorze 1551 piosenek. \
Podziału na zbiór treningowy i testowy dokonaliśmy dla każdego kompozytora osobno w proporcjach 80% treningowy - 20% testowy, tak aby w obu zbiorach znaleźli się wszyscy interesujący nas kompozytorzy, a jednocześnie nie wystąpił wyciek danych przy późniejszym dzieleniu utworów na mniejsze okna czasowe. 
#### CNN
Dla autokoderów działących na sieciach konwolucyjnych dane z formatu midi konwertowane są do postaci piano roll czyli rzadkiej macierzy o kształcie $P \times T$, gdzie $P \in \{0, ..., 127\}$ jest możliwym tonem dźwięku, który u nas ograniczyliśmy do $60$ najczęściej występujących tonów. A $T$ jest wymiarem czasu z kolejnymi próbkami w częstotliwości 60 fps, w naszym przypadku dzieliimy utwory na okna 10 sekundowe. Poszczególne wartości komórek macierzy oznaczają `velocity`, czyli dynamikę dźwięku. 

#### GRU
Dla sieci rekurencyjnych użyliśmy zapisu w skonsensowanym formacie opartym o zdarzenia. Dane zawierają informację o danej nucie w postaci $X_i \in P \times V \times S \times D$.
Gdzie $P = \{1 , \dots, 127\}$ oznacza ton nuty (również ograniczony do $60$ najczęściej występujących tonów), $V = (0, 1]$ oznacza dynamikę, $S = (0, s_{\max}]$ oznacza 
czas w sekundach pomiędzy 
naciśnięciem poprzedniego klawisza, a obecnego. $D = (0, d_{\max}]$ oznacza czas trzymania nuty w sekundach
(ograniczamy czas odstępu oraz czas trzymania nuty do  
modelu empirycznie $s_{\max} =2s, \; d_{\max} =2s$).  


### Dane wyjściowe i typ problemu
Naszym celem jest klasyfikacja kompozytorów muzyki klasycznej bazując na wycinkach z ich utworów. \
W przypadku klasyfikacji wyjściem jest u nas 20 wartości odpowiadających 20 rozważanym kompozytorom, z których maksymalną wartość uznajemy za predykcję modelu.

### Hipoteza badawacza
Jak różne podejścia będą w stanie modelować złożone zależności czasowe jakimi są nuty w klasycznych utworach muzycznych? Jak różnią się modele oparte o konwolucje od modeli rekurencyjnych w osiąganych wynikach w takim zadaniu? \
Czy jest możliwa sensowna rekonstrukcja takich zależności przez wariacyjne autokodery?

## Opis wybranego modelu
```
TODO 
- Nazwa modelu
- Publikacja, w której metoda została zaproponowana

- Bardzo zwięzły opis działania / uczenia modelu (może być rysunek z krótkim komenta-
rzem, jeśli taki jest w publikacji)

- Jeśli metoda bazuje na istniejącej – podać różnice i wprowadzone zmiany```

## Opis eksperymentów
### Metryki
Jako metrykę rekonstrukcji zastosowano funkcje straty zależne od modelu i opisane w następnej sekcji.
Dla docelowego zadania klasyfikacji zastosowano typowe dla tego zadania: accuracy, f1-score, a tak że macierze pomyłek.

### Funkcje straty
W przypadku sieci GRU zastosowano entropię krzyżową połączoną z dywergencją Kullbacka-Leiblera w sposób standardowy dla VAE. \
Natomiast dla sieci CNN dla poprawienia jakości rekonstrukcji zaproponowano własną funkcję straty zdefiniowaną jako 
$$\mathcal{L} = \mathcal{L}_{MSE} + \mathcal{L}_{Penalty} + \mathcal{L}_{D_{KL}}$$
, gdzie 
$$
\mathcal{L}_{Penalty} = \frac{1}{N} \sum_{i=1}^N \sigma\left( (y^{(i)}_{true} - m) \cdot 100 \right) \cdot \exp\left( -\lambda \frac{y^{(i)}_{pred}}{m} \right)
$$

gdzie $\sigma$ to funkcja sigmoidalna, $m = \frac{1}{127}$, $\lambda$ to siła kary, $N$ to liczba próbek, $y_{true}$ to wartości prawdziwe, a $y_{pred}$ to wartości przewidywane. \
I służy jako eksponencjalnie rosnąca kara za predykowanie zer (lub wartości mniejszych od minimalnej z zakresu MIDI) w miejscach, gdzie w rzeczywistości zera nie było. Komponent ten został wprowadzony, ponieważ ze względu na rzadką postać macierzy i zawieranie przez nią w większości zer model stawał w optimum lokalnym rekonstruującym na wyjściu same zera.

### Eksperymenty
#### VAE oparte o CNN

Przykład rekonstrukcji na zbiorze treningowym
Oryinalna próbka (train) | Rekonstrukcja (train)
:-----------------------:|:----------------------:
![](ur_assets/original_train.png) | ![](ur_assets/recon_train.png)

Przykład rekonstrukcji na zbiorze testowym
Oryinalna próbka (test) | Rekonstrukcja (test)
:-----------------------:|:----------------------:
![](ur_assets/original_test.png) | ![](ur_assets/recon_test.png)

---

Przykład rekonstrukcji na zbiorze testowym (audio)

Oryginalna próbka (test)

In [5]:
import IPython
IPython.display.Audio("data/test_original.wav")

Rekonstrukcja (test)

In [7]:
IPython.display.Audio("data/test_recon.wav")

| Model                           | Test Accuracy / F1-score |
|----------------------------------|:-------------:|
| Frozen VAE                       |     0.34      |
| Finetune VAE                     |     0.39      |
| Finetune VAE (1/2 latent)        |     0.28      |  
| End2End Autoencoder              |     0.42      |
| End2End Autoencoder (2x latent)  |     0.41      |

Macierz pomyłek dla najlepszego dostrajanego modelu VAE \
![](ur_assets/cm_vae_finetuen.png)

, gdzie kododowanie kompozytorów wygląda następująco:
| Kod | Kompozytor    |
|-----|--------------|
| 0   | Alkan        |
| 1   | Bach         |
| 2   | Beatty       |
| 3   | Beethoven    |
| 4   | Carbajo      |
| 5   | Chopin       |
| 6   | Czerny       |
| 7   | Gottschalk   |
| 8   | Handel       |
| 9   | Haydn        |
| 10  | Liszt        |
| 11  | Mozart       |
| 12  | Rebikov      |
| 13  | Scarlatti    |
| 14  | Schubert     |
| 15  | Schumann     |
| 16  | Scott        |
| 17  | Scriabin     |
| 18  | Simpson      |
| 19  | Zhang        |

Najlepiej klasyfikowanymi kompozytorami okazali się być:
- Simpson (accuracy: 0.67)
- Beatty (accuracy: 0.65)
- Liszt (accuracy: 0.55)
<br>

A tymi z którymi model miał największe problemy:
- Beethoven (accuracy: 0.20)
- Gottschalk (accuracy: 0.18)
- Alkan (accuracy: 0.08)

##### Samplowanie VAE

Dostrajane VAE daje nieco gorsze wyniki od samego autokodera uczone end2end, natomiast rozkład danych w VAE pozwala na samplowanie z jego przestrzeni ukrytej.
![](ur_assets/vae_sample.png)

In [9]:
IPython.display.Audio("data/sample_vae.wav")